In [7]:
pip install folium

In [9]:
import numpy as np
import pandas as pd
import matplotlib.pyplot as plt
import seaborn as sns
import warnings
warnings.filterwarnings('ignore')

In [11]:
terrorist = pd.read_csv('dataset\\Global_terrorist.csv', encoding='ISO-8859-1')

In [13]:
terrorist

eventid  iyear  imonth  iday approxdate  extended resolution  \
0       197000000001   1970       7     2        NaN         0        NaN   
1       197000000002   1970       0     0        NaN         0        NaN   
2       197001000001   1970       1     0        NaN         0        NaN   
3       197001000002   1970       1     0        NaN         0        NaN   
4       197001000003   1970       1     0        NaN         0        NaN   
...              ...    ...     ...   ...        ...       ...        ...   
181686  201712310022   2017      12    31        NaN         0        NaN   
181687  201712310029   2017      12    31        NaN         0        NaN   
181688  201712310030   2017      12    31        NaN         0        NaN   
181689  201712310031   2017      12    31        NaN         0        NaN   
181690  201712310032   2017      12    31        NaN         0        NaN   

        country         country_txt  region  ... addnotes  \
0            58  Dominican Republic       2  ...      NaN   
1           130              Mexico       1  ...      NaN   
2           160         Philippines       5  ...      NaN   
3            78              Greece       8  ...      NaN   
4           101               Japan       4  ...      NaN   
...         ...                 ...     ...  ...      ...   
181686      182             Somalia      11  ...      NaN   
181687      200               Syria      10  ...      NaN   
181688      160         Philippines       5  ...      NaN   
181689       92               India       6  ...      NaN   
181690      160         Philippines       5  ...      NaN   

                                                   scite1  \
0                                                     NaN   
1                                                     NaN   
2                                                     NaN   
3                                                     NaN   
4                                                     NaN   
...                                                   ...   
181686  "Somalia: Al-Shabaab Militants Attack Army Che...   
181687  "Putin's 'victory' in Syria has turned into a ...   
181688  "Maguindanao clashes trap tribe members," Phil...   
181689  "Trader escapes grenade attack in Imphal," Bus...   
181690  "Security tightened in Cotabato following IED ...   

                                                   scite2  \
0                                                     NaN   
1                                                     NaN   
2                                                     NaN   
3                                                     NaN   
4                                                     NaN   
...                                                   ...   
181686  "Highlights: Somalia Daily Media Highlights 2 ...   
181687  "Two Russian soldiers killed at Hmeymim base i...   
181688                                                NaN   
181689                                                NaN   
181690  "Security tightened in Cotabato City," Manila ...   

                                                   scite3  \
0                                                     NaN   
1                                                     NaN   
2                                                     NaN   
3                                                     NaN   
4                                                     NaN   
...                                                   ...   
181686  "Highlights: Somalia Daily Media Highlights 1 ...   
181687  "Two Russian servicemen killed in Syria mortar...   
181688                                                NaN   
181689                                                NaN   
181690                                                NaN   

                        dbsource  INT_LOG  INT_IDEO INT_MISC INT_ANY  related  
0                           PGIS        0         0        0       0      Na

In [15]:
filtered_df = terrorist[terrorist['region_txt'] == 'Middle East & North Africa']

# Filter by year (e.g., incidents after 2000)
filtered_df = filtered_df[filtered_df['iyear'] >= 2000]

# Filter by attack type (e.g., bombings)
filtered_df = filtered_df[filtered_df['attacktype1_txt'] == 'Bombing/Explosion']

# Filter by significant impact (e.g., incidents with at least 10 fatalities)
filtered_df = filtered_df[filtered_df['nkill'] >= 10]

print(f"Filtered dataset size: {len(filtered_df)} rows")

Filtered dataset size: 1737 rows


In [17]:
import folium
from folium.plugins import HeatMap

# Aggregate incidents by latitude and longitude
aggregated_df = filtered_df.groupby(['latitude', 'longitude']).size().reset_index(name='incident_count')

print(aggregated_df.head())

    latitude  longitude  incident_count
0  12.743795  44.843678               1
1  12.760069  44.890266               1
2  12.825647  44.846416              12
3  12.832581  45.027071               1
4  12.867085  44.981911               6


In [18]:
filtered_df = terrorist[(terrorist['region_txt'] == 'Middle East & North Africa') & (terrorist['iyear'] >= 2000)]

# Aggregate incidents by location
aggregated_df = filtered_df.groupby(['latitude', 'longitude']).size().reset_index(name='incident_count')

# # Normalize weights (optional)
aggregated_df['normalized_weight'] = (aggregated_df['incident_count'] - aggregated_df['incident_count'].min()) / \
                                (aggregated_df['incident_count'].max() - aggregated_df['incident_count'].min())

# Prepare heat_data
heat_data = aggregated_df[['latitude', 'longitude', 'normalized_weight']].values.tolist()

# Create a base map
m = folium.Map(location=[30, 40], zoom_start=4)

# Add heatmap layer
HeatMap(heat_data).add_to(m)

# Save or display the map
m.save('terrorism_heatmap.html')
m

<h1>REGIONAL ANALYSIS</h1>

<h1>Identify regions with the highest frequency of terrorist incidents</h1>

In [30]:
region = 'Middle East & North Africa'
filtered_df = terrorist[(terrorist['region_txt'] == region) & (terrorist['iyear'] >= 2000)]

aggregated_df = filtered_df.groupby(['latitude', 'longitude']).size().reset_index(name='incident_count')


aggregated_df['normalized_weight'] = (aggregated_df['incident_count'] - aggregated_df['incident_count'].min()) / \
                                (aggregated_df['incident_count'].max() - aggregated_df['incident_count'].min())


heat_data = aggregated_df[['latitude', 'longitude', 'normalized_weight']].values.tolist()


m = folium.Map(location=[30, 40], zoom_start=4)


HeatMap(heat_data).add_to(m)


m.save('regional_analysis_heatmap.html')
m

<h1>CRIME TYPE ANALYSIS</h1>

<h1>Understand which types of attacks are most common and where</h1>

In [25]:
attack_type = 'Bombing/Explosion'
filtered_df = terrorist[(terrorist['attacktype1_txt'] == attack_type) & (terrorist['iyear'] >= 2000)]

aggregated_df = filtered_df.groupby(['latitude', 'longitude']).size().reset_index(name='attack_count')


aggregated_df['normalized_weight'] = (aggregated_df['attack_count'] - aggregated_df['attack_count'].min()) / \
                                (aggregated_df['attack_count'].max() - aggregated_df['attack_count'].min())


heat_data = aggregated_df[['latitude', 'longitude', 'normalized_weight']].values.tolist()


m = folium.Map(location=[30, 40], zoom_start=4)


HeatMap(heat_data).add_to(m)


m.save('crime_type_analysis_heatmap.html')
m

<h1>CASUALTY ANALYSIS</h1>

<h1>Show which locations experience the most lethal attacks</h1>

In [27]:
filtered_df = terrorist[(terrorist['iyear'] >= 2000)]
filtered_df = filtered_df[['latitude', 'longitude', 'nkill']].dropna()

filtered_df['normalized_kill'] = (filtered_df['nkill'] - filtered_df['nkill'].min()) / \
                                (filtered_df['nkill'].max() - filtered_df['nkill'].min())

heat_data = filtered_df[['latitude', 'longitude', 'normalized_kill']].values.tolist()

m = folium.Map(location=[30, 40], zoom_start=4)
HeatMap(heat_data).add_to(m)
m.save('casualty_analysis_heatmap.html')
m

<h1>Demographic Analysis</h1>

<h1>Identify patterns based on perpetrators or indirect demographic implications</h1>

In [28]:
group_name = 'Taliban'
filtered_df = terrorist[(terrorist['gname'] == group_name) & (terrorist['iyear'] >= 2000)]

aggregated_df = filtered_df.groupby(['latitude', 'longitude']).size().reset_index(name='incident_count')
aggregated_df['normalized_weight'] = (aggregated_df['incident_count'] - aggregated_df['incident_count'].min()) / \
                                     (aggregated_df['incident_count'].max() - aggregated_df['incident_count'].min())
heat_data = aggregated_df[['latitude', 'longitude', 'normalized_weight']].values.tolist()

m = folium.Map(location=[30, 40], zoom_start=4)
HeatMap(heat_data).add_to(m)
m.save('demographic_proxy_analysis_heatmap.html')
m


<h1>Target Analysis</h1>

<h1>Determine which groups or sectors are being targeted most often</h1>

In [29]:
target_type = 'Military'
filtered_df = terrorist[(terrorist['targtype1_txt'] == target_type) & (terrorist['iyear'] >= 2000)]

aggregated_df = filtered_df.groupby(['latitude', 'longitude']).size().reset_index(name='incident_count')
aggregated_df['normalized_weight'] = (aggregated_df['incident_count'] - aggregated_df['incident_count'].min()) / \
                                     (aggregated_df['incident_count'].max() - aggregated_df['incident_count'].min())
heat_data = aggregated_df[['latitude', 'longitude', 'normalized_weight']].values.tolist()

m = folium.Map(location=[30, 40], zoom_start=4)
HeatMap(heat_data).add_to(m)
m.save('target_analysis_heatmap.html')
m